In [18]:
import pandas as pd
import numpy as np

In [19]:
# read data
df_en00_18 = pd.read_csv("England00_2018.csv")
df_en00_19 = pd.read_csv("England00_2019.csv")
df_en00_20 = pd.read_csv("England00_2020.csv")
df_en00_21 = pd.read_csv("England00_2021.csv")

df_it00_18 = pd.read_csv("Italy00_2018.csv")
df_it00_19 = pd.read_csv("Italy00_2019.csv")
df_it00_20 = pd.read_csv("Italy00_2020.csv")
df_it00_21 = pd.read_csv("Italy00_2021.csv")

df_sp00_18 = pd.read_csv("Spain00_2018.csv")
df_sp00_19 = pd.read_csv("Spain00_2019.csv")
df_sp00_20 = pd.read_csv("Spain00_2020.csv")
df_sp00_21 = pd.read_csv("Spain00_2021.csv")

In [20]:
# function for standings, update one match

def standing(df_standings, NH, NA, HG, AG):

    # for each team in the standings
    for i in range(len(df_standings)):

    # for home team
        if (df_standings.loc[i, 'Team'] == NH):

            df_standings.iloc[i , 1] += 1
            df_standings.iloc[i , 4] += HG
            df_standings.iloc[i , 5] += AG
            df_standings.iloc[i , 6] += HG
            df_standings.iloc[i , 7] += AG
        
            if (HG > AG):
                df_standings.iloc[i , 3] += 3
            elif (HG == AG):
                df_standings.iloc[i , 3] += 1

    # for away team
    for k in range(len(df_standings)):
    
        if (df_standings.loc[k, 'Team'] == NA):

            df_standings.iloc[k , 1] += 1
            df_standings.iloc[k , 4] += AG
            df_standings.iloc[k , 5] += HG
            df_standings.iloc[k , 8] += AG
            df_standings.iloc[k , 9] += HG
        
            if (HG < AG):
                df_standings.iloc[k , 3] += 3
            elif (HG == AG):
                df_standings.iloc[k , 3] += 1
            
    # end of the loop
    
    # the number of goals per match
    df_standings['GS_G'] = df_standings.apply(lambda x: x['GS']/x['Games'] if x['Games'] !=0 else 0, axis=1)
    df_standings['GA_G'] = df_standings.apply(lambda x: x['GA']/x['Games'] if x['Games'] !=0 else 0, axis=1)
    
    df_standings['GHS_G'] = df_standings.apply(lambda x: x['GHS']/x['Games'] if x['Games'] !=0 else 0, axis=1)
    df_standings['GHA_G'] = df_standings.apply(lambda x: x['GHA']/x['Games'] if x['Games'] !=0 else 0, axis=1)
    
    df_standings['GAS_G'] = df_standings.apply(lambda x: x['GAS']/x['Games'] if x['Games'] !=0 else 0, axis=1)
    df_standings['GAA_G'] = df_standings.apply(lambda x: x['GAA']/x['Games'] if x['Games'] !=0 else 0, axis=1)
                
    return(df_standings)     

In [21]:
# function for next match, add inf from standings
def next_match(df_standings, id_match, df_work):
    
    NH_next = df_work.loc[id_match, 'HomeTeam']
    NA_next = df_work.loc[id_match, 'AwayTeam']
    
    # for each team in the standings
    for i in range(len(df_standings)):    
        
        # for home team
        if df_standings.loc[i, 'Team'] == NH_next:
            Home_points = df_standings.loc[i,'Points']
            Home_Rank = df_standings.loc[i, 'Rank']
            Home_Goal_Score = df_standings.loc[i, 'GS_G']
            Home_Goal_Against = df_standings.loc[i, 'GA_G']
            Home_Goal_Score_home = df_standings.loc[i, 'GHS_G'] 
            Home_Goal_Against_home = df_standings.loc[i, 'GHA_G']
        # for away team    
        if df_standings.loc[i, 'Team'] == NA_next: 
            Away_points = df_standings.loc[i,'Points']
            Away_Rank = df_standings.loc[i, 'Rank']
            Away_Goal_Score = df_standings.loc[i, 'GS_G']
            Away_Goal_Against = df_standings.loc[i, 'GA_G']
            Away_Goal_Score_away = df_standings.loc[i, 'GAS_G'] 
            Away_Goal_Against_away = df_standings.loc[i, 'GAA_G']
            
    # add data in df from standings
    df_work.loc[id_match, 'HR'] = Home_Rank
    df_work.loc[id_match, 'AR'] = Away_Rank
    
    df_work.loc[id_match, 'HP'] = Home_points
    df_work.loc[id_match, 'AP'] = Away_points
    
    df_work.loc[id_match, 'DR'] = Home_Rank - Away_Rank
    df_work.loc[id_match, 'DP'] = Home_points - Away_points
    
    df_work.loc[id_match, 'HGS'] = Home_Goal_Score
    df_work.loc[id_match, 'HGA'] = Home_Goal_Against
    
    df_work.loc[id_match, 'AGS'] = Away_Goal_Score
    df_work.loc[id_match, 'AGA'] = Away_Goal_Against
    
    df_work.loc[id_match, 'HGSH'] = Home_Goal_Score_home
    df_work.loc[id_match, 'HGAH'] = Home_Goal_Against_home
    
    df_work.loc[id_match, 'AGSA'] = Away_Goal_Score_away
    df_work.loc[id_match, 'AGAA'] = Away_Goal_Against_away
    
    return(df_work)

In [22]:
# select necessary columns
# add the column with total goals 2.5

def prepare_col(df):
    df_new = df[['Div', 'Date', 'HomeTeam', 'AwayTeam', 'FTHG', 'FTAG', 'FTR', 'HTHG', 'HTAG', 
               'HS', 'AS', 'HST', 'AST', 'HF', 'AF', 'HC', 'AC', 'HY', 'AY', 'HR', 'AR',
                'B365H', 'B365D', 'B365A', 'OddUnder2.5', 'OddOver2.5']]
    
    df_new['T_2_5'] = ((df_new['FTHG'] + df_new['FTAG']) > 2.5).astype('int')
    return(df_new)

In [23]:
def prepare_df (df_work):
   
    #create df for standings
    data = {'Team':  df_work['HomeTeam'].unique(),
        'Games': 0, 'Rank': 0, 'Points': 0,
        'GS':0, 'GA':0,
        'GHS':0, 'GHA':0, 'GAS':0, 'GAA':0,
        'GS_G':0, 'GA_G':0, 'GHS_G':0, 'GHA_G':0, 'GAS_G':0, 'GAA_G':0}

    df_standings = pd.DataFrame (data, columns = ['Team','Games', 'Rank', 'Points', 
                                                  'GS', 'GA', 'GHS', 'GHA', 'GAS', 'GAA',
                                                  'GS_G', 'GA_G', 'GHS_G', 'GHA_G', 'GAS_G', 'GAA_G'])
    
    # rename columns (Total Odds) for one type
    df_work.rename(columns={'B365<2.5':'OddUnder2.5', 'B365>2.5':'OddOver2.5'}, inplace=True)
    df_work.rename(columns={'BbAv<2.5':'OddUnder2.5', 'BbAv>2.5':'OddOver2.5'}, inplace=True)
    
    
    # select important columns
    # add total, half total, second total
    # add column with results of second total 2,5 and 3,5
    df_work = prepare_col(df_work)
    
    #
    #add column for statistics of teams 
    data_additional_columns = {'Num_M': 0, 'HR': 0, 'AR': 0,  'HP': 0, 'AP': 0, 'DR': 0, 'DP': 0,
                               'HGS': 0, 'HGA': 0,  'AGS': 0, 'AGA': 0,
                               'HGSH': 0, 'HGAH': 0,  'AGSA': 0, 'AGAA': 0}
    df_work = df_work .assign(**data_additional_columns)
    
    #
    # for each matches
    for m in range(len(df_work)-1):
    
    #add number of the match
        df_work.loc[m, 'Num_M'] = m + 1
    
    # add data to next match in work DF from standings
    
        if (m < (len(df_work)-1)): 
            next_match(df_standings, m, df_work)
     
    # upload data in standing by match results
        NG = df_work.loc[m, 'HomeTeam']
        NA = df_work.loc[m, 'AwayTeam']
    
        HG = df_work.loc[m, 'FTHG']
        AG = df_work.loc[m, 'FTAG']
        standing(df_standings, NG, NA, HG, AG)
    
        df_standings = df_standings.sort_values(by=['Points'], ascending=False).reset_index(drop=True)
        
        for l in range(len(df_standings)):
            df_standings.loc[l, 'Rank'] = l + 1
        
    return(df_work) 

In [24]:
# create df (train and test)
df_finish_it18 = prepare_df(df_it00_18)
df_finish_it19 = prepare_df(df_it00_19)
df_finish_it20 = prepare_df(df_it00_20)
df_train_it = pd.concat([df_finish_it18, df_finish_it19, df_finish_it20]) 
df_test_it = prepare_df(df_it00_21)


df_finish_en18 = prepare_df(df_en00_18)
df_finish_en19 = prepare_df(df_en00_19)
df_finish_en20 = prepare_df(df_en00_20)
df_train_en = pd.concat([df_finish_en18, df_finish_en19, df_finish_en20])
df_test_en = prepare_df(df_en00_21)


df_finish_sp18 = prepare_df(df_sp00_18)
df_finish_sp19 = prepare_df(df_sp00_19)
df_finish_sp20 = prepare_df(df_sp00_20)
df_train_sp = pd.concat([df_finish_sp18, df_finish_sp19, df_finish_sp20])
df_test_sp = prepare_df(df_sp00_21)

<ipython-input-22-d46773e1faac>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_new['T_2_5'] = ((df_new['FTHG'] + df_new['FTAG']) > 2.5).astype('int')
<ipython-input-22-d46773e1faac>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_new['T_2_5'] = ((df_new['FTHG'] + df_new['FTAG']) > 2.5).astype('int')
<ipython-input-22-d46773e1faac>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in

In [26]:
# check a balanc of classes
df_train_en['T_2_5'].value_counts()

1    596
0    544
Name: T_2_5, dtype: int64

In [28]:
df_test_it = df_test_it.dropna().reset_index(drop = True)

In [30]:
# function for split on X and Y for fiting model

def split_data (df):

    y = df['T_2_5']

    X = df.drop(['Div', 'Date', 'HomeTeam', 'AwayTeam', 
                            'FTHG', 'FTAG', 'FTR', 'HTHG', 'HTAG', 'T_2_5'], axis =1)

    # without stats of teams during matchs (kicks, fouls and other)
    X_without_stats = df[['B365H', 'B365D', 'B365A', 'OddUnder2.5', 'OddOver2.5',
                          'Num_M', 'HP', 'AP', 'DR', 'DP',
                          'HGS', 'HGA', 'AGS', 'AGA', 'HGSH', 'HGAH', 'AGSA', 'AGAA']]
    return(y, X, X_without_stats)

In [31]:
# split data for model
y_en_train, X_en_train, X_without_en_train = split_data(df_train_en)
y_en_test, X_en_test, X_without_en_test = split_data(df_test_en)

y_it_train, X_it_train, X_without_it_train = split_data(df_train_it)
y_it_test, X_it_test, X_without_it_test = split_data(df_test_it)

y_sp_train, X_sp_train, X_without_sp_train = split_data(df_train_sp)
y_sp_test, X_sp_test, X_without_sp_test = split_data(df_test_sp)

In [32]:
from matplotlib import pyplot
from sklearn import tree
from sklearn.tree import DecisionTreeClassifier
from sklearn import datasets
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from sklearn import metrics
from sklearn.metrics import confusion_matrix
from sklearn.metrics import precision_score, recall_score
from sklearn.metrics import accuracy_score
from sklearn.ensemble import RandomForestClassifier

from sklearn.metrics import classification_report
from xgboost import XGBClassifier

In [33]:
# Desicion Tree

In [34]:
def DTC_model(X, y):
    
    # model
    dtc=DecisionTreeClassifier(random_state=42)
    
    # parameters for GridSearch
    param_grid = { 
        'criterion': ['gini'],
        'max_features': ['auto'],
        'max_depth': [6,7,8,9,10],
        'min_samples_leaf': range(1, 4)
    }
    
    cv_dtc = GridSearchCV(cv=5, estimator=dtc, param_grid=param_grid)
    cv_dtc.fit(X, y)
    
    best_dtc = cv_dtc.best_estimator_
    
    return(best_dtc)

In [35]:
#Random Forest

In [36]:
def RFC_model(X, y):
    
    # model
    rfc=RandomForestClassifier(random_state=42)
    # parameters for GridSearch
    param_grid = { 
        'criterion': ['gini'],
        'n_estimators': [90, 100, 110],
        'max_features': ['auto'],
        'max_depth': [5,6,7,8],
        'min_samples_leaf': range(2, 4)
    }
    
    cv_rfc = GridSearchCV(cv=5, estimator=rfc, param_grid=param_grid)
    cv_rfc.fit(X, y)
    best_rfc = cv_rfc.best_estimator_
    
    return(best_rfc)

In [37]:
#XGBoost

In [38]:
def XGB_model(X, y):
    
    # model
    xgb_model = XGBClassifier(objective = 'binary:logistic')
    # parameters for GridSearch
    param_grid = { 
        'n_estimators': [25, 30, 40],
        'max_depth': [4,5,6,7],
        'learning_rate' :[0.2, 0.3],
        'alpha' : [9, 10, 11, 12, 13]
    }
    
    cv_xgb = GridSearchCV(cv=5, estimator=xgb_model, param_grid=param_grid)
    cv_xgb.fit(X, y)
    best_xgb = cv_xgb.best_estimator_
    
    return(best_xgb)

In [39]:
#
def Bookmakers_model(X, y):
    temp = (X['OddOver2.5'] < X['OddUnder2.5']).astype('int')
    return(pd.DataFrame([accuracy_score(y,  temp)], columns = ['01']))
    

In [41]:
def estimate_profit(df):
    for i in range(len(df)):
        if (df.loc[i, 'Predict_Total'] == df.loc[i, 'T_2_5']):
 #           df.loc[i, 'profit'] = 1
            if (df.loc[i, 'Predict_Total'] == 1):
                df.loc[i, 'profit'] = df.loc[i, 'OddOver2.5'] - 1
            else :
                df.loc[i, 'profit'] = df.loc[i, 'OddUnder2.5'] - 1
        else :
            df.loc[i, 'profit'] = -1
#    df['profit'].sum()
    return (df)

In [42]:
# Profit for model
def sum_profit(model, df, X):
    df['Predict_Total'] = model.predict(X)
#    df_work_test['Predict_Total'].value_counts()
    estimate_profit(df)
    return((df['profit'].sum())/(len(df)))

In [43]:
# function for estamate accuracy for train and test dataset
def score (clr, X_train, y_train, X_test, y_test):
    clr.fit(X_train, y_train)
    data = np.array([[clr.score(X_train, y_train)],
                    [clr.score(X_test, y_test)]])
    df = pd.DataFrame(data, columns = ['01'])
    return(df)

In [44]:
#function profit bookmakers
def profit_bookmakers (df):
    df['Predict_Total_Bookmakers'] = (df['OddOver2.5'] < df['OddUnder2.5']).astype('int')
    for i in range(len(df)):
        if (df.loc[i, 'Predict_Total_Bookmakers'] == df.loc[i, 'T_2_5']):
            if (df.loc[i, 'Predict_Total_Bookmakers'] == 1):
                df.loc[i, 'profit_bm'] = df.loc[i, 'OddOver2.5'] - 1
            else :
                df.loc[i, 'profit_bm'] = df.loc[i, 'OddUnder2.5'] - 1
        else :
            df.loc[i, 'profit_bm'] = -1
    return((df['profit_bm'].sum())/(len(df)))

In [45]:
#Fiting model and estimating score for England
df_result_DTC_en = score(DTC_model(X_en_train, y_en_train), X_en_train, y_en_train, X_en_test, y_en_test)
df_result_RFC_en = score(RFC_model(X_en_train, y_en_train), X_en_train, y_en_train, X_en_test, y_en_test)
df_result_XGB_en = score(XGB_model(X_en_train, y_en_train), X_en_train, y_en_train, X_en_test, y_en_test)
df_result_XGB_without_stats_en = score(XGB_model(X_without_en_train,y_en_train), 
                       X_without_en_train, y_en_train, X_without_en_test , y_en_test)
df_result_bookmakers_en = Bookmakers_model(X_en_test, y_en_test)

df_result_en = pd.concat([df_result_DTC_en, df_result_RFC_en, df_result_XGB_en, df_result_XGB_without_stats_en,
                         df_result_bookmakers_en])


C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[14:42:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:42:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:42:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:42:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:42:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:42:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:42:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:42:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

...

[14:43:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:43:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:43:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:43:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:43:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:43:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:43:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:43:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:43:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:43:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:43:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


In [46]:
#Fiting model and estimating score for Italy
df_result_DTC_it = score(DTC_model(X_it_train, y_it_train), X_it_train, y_it_train, X_it_test, y_it_test)
df_result_RFC_it = score(RFC_model(X_it_train, y_it_train), X_it_train, y_it_train, X_it_test, y_it_test)
df_result_XGB_it = score(XGB_model(X_it_train, y_it_train), X_it_train, y_it_train, X_it_test, y_it_test)
df_result_XGB_without_stats_it = score(XGB_model(X_without_it_train,y_it_train), 
                       X_without_it_train, y_it_train, X_without_it_test , y_it_test)
df_result_bookmakers_it = Bookmakers_model(X_it_test, y_it_test)

df_result_it = pd.concat([df_result_DTC_it, df_result_RFC_it, df_result_XGB_it, df_result_XGB_without_stats_it,
                         df_result_bookmakers_it])

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:44:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:44:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:44:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:44:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:44:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:44:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:44:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:44:25] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

...

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:45:38] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:45:38] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:45:38] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:45:38] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:45:38] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:45:38] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:45:39] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:45:39] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

In [47]:
#Fiting model and estimating score for Spain
df_result_DTC_sp = score(DTC_model(X_en_train, y_en_train), X_en_train, y_en_train, X_en_test, y_en_test)
df_result_RFC_sp = score(RFC_model(X_en_train, y_en_train), X_en_train, y_en_train, X_en_test, y_en_test)
df_result_XGB_sp = score(XGB_model(X_en_train, y_en_train), X_en_train, y_en_train, X_en_test, y_en_test)
df_result_XGB_without_stats_sp = score(XGB_model(X_without_sp_train,y_sp_train), 
                       X_without_sp_train, y_sp_train, X_without_sp_test , y_sp_test)
df_result_bookmakers_sp = Bookmakers_model(X_sp_test, y_sp_test)

df_result_sp = pd.concat([df_result_DTC_sp, df_result_RFC_sp, df_result_XGB_sp, df_result_XGB_without_stats_sp,
                         df_result_bookmakers_sp])

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:46:12] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:46:12] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:46:12] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:46:12] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:46:13] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:46:13] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:46:13] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:46:13] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

...

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:47:21] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:47:21] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:47:21] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:47:21] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:47:21] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:47:21] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:47:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:47:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


In [48]:
data = {'Name':['DecesionTree_train', 'DecesionTree_test', 
                'RandomForest_train', 'RandomForest_test',
                'XGBoost_train', 'XGBoost_test', 
                'XGBoost_without_stats_train', 'XGBoost_without_stats_test',
               'Bookmakers'],
        'England':  df_result_en['01'],
        'Italy': df_result_it['01'],
        'Spain': df_result_sp['01']
       }

df_result = pd.DataFrame (data, 
                          columns = ['Name','England', 'Italy', 'Spain']).reset_index(drop=True)

In [49]:
df_result


Name   England     Italy     Spain
0           DecesionTree_train  0.773684  0.720175  0.773684
1            DecesionTree_test  0.555172  0.478102  0.555172
2           RandomForest_train  0.827193  0.842105  0.827193
3            RandomForest_test  0.620690  0.664234  0.620690
4                XGBoost_train  0.752632  0.763158  0.752632
5                 XGBoost_test  0.631034  0.675182  0.631034
6  XGBoost_without_stats_train  0.690351  0.696491  0.703509
7   XGBoost_without_stats_test  0.555172  0.565693  0.585714
8                   Bookmakers  0.568966  0.580292  0.592857

In [50]:
# PROFIT England

model = XGB_model(X_en_train, y_en_train)
model_without_stat = XGB_model(X_without_en_train, y_en_train)


data = np.array([[sum_profit(model, df_test_en, X_en_test)],
                [sum_profit(model_without_stat, df_test_en, X_without_en_test)],
                [profit_bookmakers(df_test_en)]])
df_en_profit = pd.DataFrame(data, columns = ['01'])


C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:53:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:53:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:53:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:53:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:53:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:53:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:53:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:53:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

...

[14:54:34] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:54:34] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:54:34] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:54:34] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:54:34] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:54:34] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:54:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:54:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:54:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:54:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:54:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


In [51]:
# PROFIT Italy
model = XGB_model(X_it_train, y_it_train)
model_without_stat = XGB_model(X_without_it_train, y_it_train)


data = np.array([[sum_profit(model, df_test_it, X_it_test)],
                [sum_profit(model_without_stat, df_test_it, X_without_it_test)],
                [profit_bookmakers(df_test_it)]])
df_it_profit = pd.DataFrame(data, columns = ['01'])

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:55:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:55:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:55:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:55:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:55:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:55:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:55:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:55:33] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

...

[14:56:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:56:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:56:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:56:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:56:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:56:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:56:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:56:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:56:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:56:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:56:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:56:35] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [52]:
# PROFIT Spain
model = XGB_model(X_sp_train, y_sp_train)
model_without_stat = XGB_model(X_without_sp_train, y_sp_train)


data = np.array([[sum_profit(model, df_test_sp, X_sp_test)],
                 [sum_profit(model_without_stat, df_test_sp, X_without_sp_test)],
                 [profit_bookmakers(df_test_sp)]])
df_sp_profit = pd.DataFrame(data, columns = ['01'])

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:56:36] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:56:36] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:56:36] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:56:36] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:56:36] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:56:36] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:56:37] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:56:37] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

...

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:57:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:57:45] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:57:45] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:57:45] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgb

[14:57:45] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:57:45] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[14:57:45] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


C:\Users\Admin\anaconda3\envs\tensorflow\lib\site-packages\xgboost\sklearn.py:888: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


In [53]:
data_profit = {'Name':['Profit_with_stats', 'Profit', 'Profit_Bookmakers'],
        'England':  df_en_profit['01'],
        'Italy': df_it_profit['01'],
        'Spain': df_sp_profit['01']
       }

df_result_profit = pd.DataFrame (data_profit, 
                          columns = ['Name','England', 'Italy', 'Spain'])

In [54]:
df_result_profit

Name   England     Italy     Spain
0  Profit_with_stats  0.175862  0.216825  0.279571
1             Profit -0.028414 -0.056752 -0.013607
2  Profit_Bookmakers -0.030724 -0.045036 -0.035893